# Tutorial to using CPlantBox
CPlantBox can be used to create plant topological and geometrical structures. An experienced used could create a strcture in one hour. There are generally three ways to use CPlantBox, whcih are :

1. Cloud based GUI without any coding
2. Jupyternote based python scripting (cloud or local)
3. Hardcore c++ using/development

Here we focusing on the 2nd way (my favourite way), in this tutorial, you could learn:

1. Two ways to setup parameter file (3 minutes)
2. How to change parameters in a single organ (10 minutes)
3. How to connect different organs to make a whole plant (10 minutes)
4. Specific organ subTypes and what are they used for (2 minutes)
5. Post processing of CPlantBox i.e. Paraview animation/ PiafMunch coupling (5 minutes)

## 1.1 Loading libraries
The jupyter notebook version of CPlantBox needs quite a lot of python libraries to run.
They are written in the requirements.txt file listed in the root folder. To load all of them, I worte a script to load them once at the beginning of the notebook:

In [1]:
# loading libraries, you need to run it only once when using the notebook
from CPlantBox_PiafMunch import *

## 1.2  XML file parameter
Like most of the models, CPlantBox rely on parameters to make a plant. 
In the first example, the use the XML file that was prepared beforehand  

In [105]:
%%time
# Read XML and make plants:
# Step 1: make a plant object
p = pb.Plant()
# Step 2: read XML parameters
p.openXML('../../modelparameter/plant/small_2020.xml')
# p.openXML('../../modelparameter/plant/leaf_alternate.xml')

# p.openXML('../../modelparameter/plant/logo_plant.xml')

# initialize
p.initialize()
# simulation for 10 days
# p.simulate(30) 

p.simulate(3) 
# Visualize it
fig = visual_plant_l(p)
fig.show()

# output of vtp, used for postprocessing and animation
p.write("output.vtp")

CPU times: user 31.2 ms, sys: 31.2 ms, total: 62.5 ms
Wall time: 62 ms


## 1.3  Python parameter

there are 4 types of organs, seed, root, stem and leaf
we can creat seed parameter:

In [ ]:
srp = pb.SeedRandomParameter(p)  # with default values

To look at the parameters, we can use:

In [45]:
print(srp)

[Parameters of undefined]
Variable		Value		Deviation		Description
===
maxTi             	0		0			Maximal number of tillers [1]
organType         	1		-			Organ type (unspecified organ = 0, seed = 1, root = 2, stem = 3, leaf = 4)
subType           	0		-			Unique identifier of this sub type
a                 	0.1		0			Root radius [cm]
delayB            	0		0			Time delay between the basal roots [day]
delayRC           	1e+09		0			Delay between the root crowns [day]
delaySB           	1e+09		0			Time delay between the shoot borne roots [day]
firstB            	0		0			Emergence of first basal root [day]
firstSB           	1e+09		0			First emergence of a shoot borne root [day]
maxB              	0		0			Maximal number of basal roots [1]
nC                	0		0			Maximal number of roots per root crown [1]
nz                	1		0			Distance between the root crowns along the shoot [cm]
seedPos.x         	0		0			X-Coordinate of seed position [cm]
seedPos.y         	0		0			Y-Coordinate of seed posi

to make a plant read a parameter, we use 

In [46]:
p.setOrganRandomParameter(srp)

## 2.1 Simple 1 single root creation
To create a single root, we need first a seed, whcich make sense.
1. Seed parameter affect roots:
* seed position
* basal root
* shoot born root or crown root


* tropismT: type of tropism

In [107]:
p = pb.Plant()

################### seed parameter #####################
srp = pb.SeedRandomParameter(p)  # with default values
srp.seedPos = pb.Vector3d(0., 0., -3.)  # [cm] seed position
srp.maxB = 0  # [-] number of basal roots (neglecting basal roots and shoot borne)
# srp.maxB = 2  # [-] number of basal roots (neglecting basal roots and shoot borne)

srp.firstB = 0  # [day] first emergence of a basal root
srp.delayB = 0  # [day] delay between the emergence of basal roots

# srp.firstB = 4  # [day] first emergence of a basal root
# srp.delayB = 2  # [day] delay between the emergence of basal roots

srp.maxTil = 0 # [-] number of tills 

srp.nC = 0  # Maximal number of roots per root crown [1]

# srp.nZ = 0 # Distance between the root crowns along the shoot [cm]
srp.nCs = 0
p.setOrganRandomParameter(srp)

################### root organ parameter #####################
r0 = pb.RootRandomParameter(p)  # with default values,

r0.name = "taproot"
r0.subType = 1  # [-] index starts at 1, 4 is basal root, 5 is shoot-born-root


r0.lmax = 90  # [cm] maximal root length, number of lateral branching nodes = round((lmax-lb-la)/ln) + 1
r0.a = 0.2  # [cm] radius
r0.dx = 0.25  # [cm] axial resolution
r0.theta = 0.  # [rad]
r0.r = 1  # [cm/day] initial growth rate



r0.tropismT = pb.TropismType.gravi  #
r0.tropismN = 1.8  # [-] strength of tropism
r0.tropismS = 0.2  # [rad/cm] maximal bending


r0.lb = 5  # [cm] basal zone
r0.la = 10  # [cm] apical zone
r0.ln = 1.  # [cm] inter-lateral distance (16 branching nodes)

p.setOrganRandomParameter(r0)



################### running simulation #####################
p.initialize()
p.simulate(10)
# fig = visual_plant_l(p)


In [108]:
# here you should see a single long root
fig = visual_plant_l(p, 'sub_types')
fig.show()

2. Root parameters only affect itself
* name (not important)
* subtype (very important: 1 is the tap/main organ, some numbers are blocked for sepcific use, be careful!)
* lmax: maximal lenghth
* a: radius
* dx: resolution
* theta: insertion angle
* r: growth rate

that root reached -12 cm, can we make it shorter?
there are three ways to make it shorter
1. reduce lmax
2. reduce simulation time
3. reduce growth rate

can we make it thicker?
* using a: radius


In [109]:
r0.lmax = 10  # [cm] maximal root length, number of lateral branching nodes = round((lmax-lb-la)/ln) + 1
r0.r = 1
r0.a = 0.5 # make it thicker


p.setOrganRandomParameter(r0)
p.initialize()

p.simulate(10)
# p.simulate(1)

fig = visual_plant_l(p)
fig.show()


can we bend it more?
* use theta to make it incline
* use tropism to make it bend

In [110]:
r0.theta = 1

r0.tropismT = 1 
r0.tropismN = 1.8  # [-] strength of tropism
r0.tropismS = 0.2  # [rad/cm] maximal bending

p.setOrganRandomParameter(r0)
p.initialize()
p.simulate(20)
# p.simulate(1)
fig = visual_plant_l(p)
fig.show()

Now you almost mastered the single root
let's add some laterals
1. you need a lateral organ


In [111]:
################### root organ parameter #####################
r1 = pb.RootRandomParameter(p)  # with default values,

r1.name = "1st lateral"

########## unique identifier in the same organ ##############
r1.subType = 2  # [-] index starts at 1, 4 is basal root, 5 is shoot-born-root


r1.lmax = 50  # [cm] maximal root length, number of lateral branching nodes = round((lmax-lb-la)/ln) + 1
r1.a = 0.3  # [cm] radius
r1.dx = 0.25  # [cm] axial resolution
r1.theta = 0.3  # [rad]
r1.r = 1  # [cm/day] initial growth rate



r1.tropismT = 2  #
r1.tropismN = 1.8  # [-] strength of tropism
r1.tropismS = 0.2  # [rad/cm] maximal bending


r1.lb = 5  # [cm] basal zone
r1.la = 10  # [cm] apical zone
r1.ln = 1.  # [cm] inter-lateral distance (16 branching nodes)

2. adding it as successor to the parent organ

In [112]:
r0.lmax =80
r0.successor = [2]  # add successors
r0.successorP = [1]  # probability that successor emerges

r0.lb = 5  # [cm] basal zone
r0.la = 10  # [cm] apical zone
r0.ln = 5.  # [cm] inter-lateral distance (16 branching nodes)

r1.lmax = 20

p.setOrganRandomParameter(r0)
p.setOrganRandomParameter(r1)
p.initialize()
p.simulate(140)
# p.simulate(1)
fig = visual_plant_l(p, 'sub_types')
fig.show()

Now we can add stem similarly to root

In [113]:
s1 = pb.StemRandomParameter(p)
s1.name = "mainstem"
s1.a =0.5
s1.subType = 1
s1.lmax = 106
s1.lb = 90
s1.la = 1
s1.ln = 7
s1.lnf = 0
s1.RotBeta = 0.5
s1.BetaDev = 0
s1.InitBeta = 0
s1.gf = 1

s1.theta = 0.


s1.tropismT = 4
s1.tropismN = 2
s1.tropismS = 0.1
s1.r = 3

s1.successor = [5]
s1.successorP = [1]

p.setOrganRandomParameter(s1)

p.initialize()
p.simulate(40)
# p.simulate(1)
fig = visual_plant_l(p)
fig.show()
# l1 = pb.LeafRandomParameter(p)

In [114]:
s5 = pb.StemRandomParameter(p)
s5.name = "horizontal_stem"
s5.subType = 5
s5.lmax = 70
s5.lb = 0
s5.la = 2
s5.ln = 15
s5.lnf = 0
s5.RotBeta = 0.5
s5.BetaDev = 0
s5.InitBeta = 0
s5.gf = 1
s5.a = 0.4
# s5.successor = [3]
# s5.successorP = [1]
s5.tropismT = 5
s5.theta = 0.5
s5.tropismN = 18
s5.tropismS = 0.01
s5.r =3

p.setOrganRandomParameter(s5)

p.initialize()
p.simulate(140)
# p.simulate(1)
fig = visual_plant_l(p)
fig.show()
# l1 = pb.LeafRandomParameter(p)

Based on the previous example, we can try to create a lyre system
![grape](https://media.winefolly.com/grapevine-training-methods.jpg)

In [149]:
s5 = pb.StemRandomParameter(p)
s5.name = "horizontal_stem"
s5.subType =5
s5.lmax = 30
s5.lb = 22
s5.la = 2
s5.ln = 3
s5.lnf = 0
s5.RotBeta = 0.5
s5.BetaDev = 0
s5.InitBeta = 0
s5.gf = 1
s5.a = 0.4
s5.successor = [3]
s5.successorP = [1]
s5.tropismT = 5
s5.theta = 0.5
s5.tropismN = 18
s5.tropismS = 0.01
s5.r =3




s3 = pb.StemRandomParameter(p)
s3.name = "2nd horizontal stem"
s3.subType = 3
s3.a =0.3
s3.lb = 2
s3.lmax = 50
s3.la = 1
s3.ln = 10
s3.lnf = 0
s3.RotBeta = 0.5
s3.BetaDev = 0
s3.InitBeta = 1
s3.theta = 0.5
s3.gf = 1
s3.tropismT = 0
s3.successor = [7]
s3.successorP = [1]
s3.tropismN = 18
s3.tropismS = 0.01
s3.r = 8

s7 = pb.StemRandomParameter(p)
s7.name = "1_year_stem"
s7.a = 0.3
s7.subType = 7
s7.lmax = 60
s7.lb = 0
s7.la = 2
s7.ln = 20
s7.lnf = 5
s7.RotBeta =0
s7.BetaDev = 0
s7.InitBeta = 0
s7.gf = 1
s7.successor = [2]
s7.successorP = [1]
s7.tropismT = 1
s7.theta = 0.5
s7.tropismN = 200
s7.tropismS = 0.2
s7.r =3


s2 = pb.StemRandomParameter(p)
s2.name = "bud"
s2.subType = 2
s2.lb = 0
s2.lmax = 0
s2.la = 0
s2.ln = 5
s2.lnf = 0
s2.RotBeta = 0
s2.BetaDev = 0
s2.InitBeta = 0.
s2.theta = 0.5
s2.gf = 1
s2.tropismT = 4
s2.tropismN = 18
s2.tropismS = 2
s2.r = 3


l1 = pb.LeafRandomParameter(p)
l1.name = 'leaf_under_second_stem'
l1.a= 2
l1.subType = 2
l1.lb = 2
l1.la = 0.2
l1.lmax = 5
l1.r = 0.5
l1.lnf = 5
l1.RotBeta = 0.5
l1.BetaDev = 0
l1.InitBeta = 0.5
l1.tropismT = 1
l1.tropismN = 5
l1.tropismS = 0.15
l1.theta = 0.35
l1.gf = 1









p.setOrganRandomParameter(s5)
p.setOrganRandomParameter(s3)
p.setOrganRandomParameter(l1)
p.setOrganRandomParameter(s2)
p.setOrganRandomParameter(s7)

p.initialize()
p.simulate(140)
# p.simulate(1)
fig = visual_plant_l(p)
fig.show()
# l1 = pb.LeafRandomParameter(p)

can you quickly change it to the curtain? how many parameters do you need to change?

In [150]:
s7.tropismT = 1
p.setOrganRandomParameter(s7)

p.initialize()
p.simulate(140)
# p.simulate(1)
fig = visual_plant_l(p)
fig.show()
# l1 = pb.LeafRandomParameter(p)

In [ ]:
from IPython.display import HTML
HTML('GeometryViewer.html')